![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Systemy Dialogowe </h1>
<h2> 8. <i>Parsing semantyczny z wykorzystaniem technik uczenia maszynowego</i>  [laboratoria]</h2> 
<h3> Marek Kubis (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Parsing semantyczny z wykorzystaniem technik uczenia maszynowego
================================================================

Wprowadzenie
------------
Problem wykrywania slotów i ich wartości w wypowiedziach użytkownika można sformułować jako zadanie
polegające na przewidywaniu dla poszczególnych słów etykiet wskazujących na to czy i do jakiego
slotu dane słowo należy.

> chciałbym zarezerwować stolik na jutro**/day** na godzinę dwunastą**/hour** czterdzieści**/hour** pięć**/hour** na pięć**/size** osób

Granice slotów oznacza się korzystając z wybranego schematu etykietowania.

### Schemat IOB

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |

> chciałbym zarezerwować stolik na jutro**/B-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/I-hour** na pięć**/B-size** osób

### Schemat IOBES

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |
| E      | koniec slotu (ending)      |
| S      | pojedyncze słowo (single)  |

> chciałbym zarezerwować stolik na jutro**/S-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/E-hour** na pięć**/S-size** osób

Jeżeli dla tak sformułowanego zadania przygotujemy zbiór danych
złożony z wypowiedzi użytkownika z oznaczonymi slotami (tzw. *zbiór uczący*),
to możemy zastosować techniki (nadzorowanego) uczenia maszynowego w celu zbudowania modelu
annotującego wypowiedzi użytkownika etykietami slotów.

Do zbudowania takiego modelu można wykorzystać między innymi:

 1. warunkowe pola losowe (Lafferty i in.; 2001),

 2. rekurencyjne sieci neuronowe, np. sieci LSTM (Hochreiter i Schmidhuber; 1997),

 3. transformery (Vaswani i in., 2017).

Przykład
--------
Skorzystamy ze zbioru danych przygotowanego przez Schustera (2019).

Zbiór ten gromadzi wypowiedzi w trzech językach opisane slotami dla dwunastu ram należących do trzech dziedzin `Alarm`, `Reminder` oraz `Weather`. Dane wczytamy korzystając z biblioteki [conllu](https://pypi.org/project/conllu/).

In [7]:
from conllu import parse_incr
fields = ['id', 'form', 'frame', 'slot']

def nolabel2o(line, i):
    return 'O' if line[i] == 'NoLabel' else line[i]
# pathTrain = '../tasks/zad8/en/train-en.conllu'
# pathTest = '../tasks/zad8/en/test-en.conllu'

pathTrain = '../tasks/zad8/pl/train.conllu'
pathTest = '../tasks/zad8/pl/test.conllu'

with open(pathTrain, encoding="UTF-8") as trainfile:
    i=0
    for line in trainfile:
        print(line)
        i+=1
        if i==15: break 
    trainset = list(parse_incr(trainfile, fields=fields, field_parsers={'slot': nolabel2o}))
with open(pathTest,  encoding="UTF-8") as testfile:
    testset = list(parse_incr(testfile, fields=fields, field_parsers={'slot': nolabel2o}))
    

# text: halo			

# intent: hello			

# slots: 			

1	halo	hello	NoLabel

			

# text: chaciałbym pójść na premierę filmu jakie premiery są w tym tygodniu			

# intent: reqmore			

# slots: 			

1	chaciałbym	reqmore	NoLabel

2	pójść	reqmore	NoLabel

3	na	reqmore	NoLabel

4	premierę	reqmore	NoLabel

5	filmu	reqmore	NoLabel

6	jakie	reqmore	B-goal

7	premiery	reqmore	I-goal



Zobaczmy kilka przykładowych wypowiedzi z tego zbioru.

In [2]:
from tabulate import tabulate
tabulate(trainset[1], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>wybieram</td><td>inform</td><td>O      </td></tr>\n<tr><td style="text-align: right;">2</td><td>batmana </td><td>inform</td><td>B-title</td></tr>\n</tbody>\n</table>'

In [3]:
tabulate(trainset[16], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>chcę        </td><td>inform</td><td>O     </td></tr>\n<tr><td style="text-align: right;">2</td><td>zarezerwować</td><td>inform</td><td>B-goal</td></tr>\n<tr><td style="text-align: right;">3</td><td>bilety      </td><td>inform</td><td>O     </td></tr>\n</tbody>\n</table>'

In [4]:
tabulate(trainset[20], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>chciałbym </td><td>inform</td><td>O</td></tr>\n<tr><td style="text-align: right;">2</td><td>anulować  </td><td>inform</td><td>O</td></tr>\n<tr><td style="text-align: right;">3</td><td>rezerwację</td><td>inform</td><td>O</td></tr>\n<tr><td style="text-align: right;">4</td><td>biletu    </td><td>inform</td><td>O</td></tr>\n</tbody>\n</table>'

Budując model skorzystamy z architektury opartej o rekurencyjne sieci neuronowe
zaimplementowanej w bibliotece [flair](https://github.com/flairNLP/flair) (Akbik i in. 2018).

In [4]:
from flair.data import Corpus, Sentence, Token
from flair.datasets import SentenceDataset, CSVClassificationCorpus
from flair.embeddings import StackedEmbeddings
from flair.embeddings import WordEmbeddings
from flair.embeddings import CharacterEmbeddings
from flair.embeddings import FlairEmbeddings
from flair.models import SequenceTagger
from flair.trainers import ModelTrainer
from flair.datasets import DataLoader
import flair
# determinizacja obliczeń
import random
import torch
random.seed(42)
torch.manual_seed(42)

if torch.cuda.is_available():
    torch.cuda.manual_seed(0)
    torch.cuda.manual_seed_all(0)
    torch.backends.cudnn.enabled = False
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

In [5]:
flair.__version__
# Python 3.8.3 

'0.6.1'

Dane skonwertujemy do formatu wykorzystywanego przez `flair`, korzystając z następującej funkcji.

In [30]:
def conllu2flair(sentences, label1=None, label2=None):
    fsentences = []

    for sentence in sentences:
        fsentence = Sentence()

        for token in sentence:
            ftoken = Token(token['form'])

            if label1:
                if label2:
                    ftoken.add_tag(label1, token[label1] + "/" + token[label2])
                else:
                    ftoken.add_tag(label1, token[label1])
                    
            fsentence.add_token(ftoken)

        fsentences.append(fsentence)

    return SentenceDataset(fsentences)

corpus = Corpus(train=conllu2flair(trainset, 'slot'), test=conllu2flair(testset, 'slot'))
print(corpus)
tag_dictionary = corpus.make_tag_dictionary(tag_type='slot')
print(tag_dictionary)

Corpus: 346 train + 38 dev + 32 test sentences
Dictionary with 20 tags: <unk>, O, B-interval, I-interval, B-title, B-date, I-date, B-time, B-quantity, B-area, I-area, B-goal, I-goal, I-title, I-time, I-quantity, B-seats, I-seats, <START>, <STOP>


Nasz model będzie wykorzystywał wektorowe reprezentacje słów (zob. [Word Embeddings](https://github.com/flairNLP/flair/blob/master/resources/docs/TUTORIAL_3_WORD_EMBEDDING.md)).

In [31]:
embedding_types = [
    WordEmbeddings('pl'),
    FlairEmbeddings('polish-forward'),
    FlairEmbeddings('polish-backward'),
    CharacterEmbeddings(),
]

embeddings = StackedEmbeddings(embeddings=embedding_types)
tagger = SequenceTagger(hidden_size=256, embeddings=embeddings,
                        tag_dictionary=tag_dictionary,
                        tag_type='slot', use_crf=True)

Zobaczmy jak wygląda architektura sieci neuronowej, która będzie odpowiedzialna za przewidywanie
slotów w wypowiedziach.

In [8]:
print(tagger)

SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dropout): LockedDropout(p=0.5)
  (embedding2nn): Linear(in_features=4446, out_features=4446, bias=True)
  (rnn): LSTM(4446, 256, batch_first=True, bidirectiona

Wykonamy dziesięć iteracji (epok) uczenia a wynikowy model zapiszemy w katalogu `slot-model`.

In [44]:
modelPath = 'slot-model/final-model.pt'

from os.path import exists

fileExists = exists(modelPath)

if(not fileExists):
    trainer = ModelTrainer(tagger, corpus)
    trainer.train('slot-model',
                learning_rate=0.1,
                mini_batch_size=32,
                max_epochs=10,
                train_with_dev=False)

Jakość wyuczonego modelu możemy ocenić, korzystając z zaraportowanych powyżej metryk, tj.:

 - *tp (true positives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fp (false positives)*

   > liczba słów nieoznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fn (false negatives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, którym model nie nadał etykiety $e$

 - *precision*

   > $$\frac{tp}{tp + fp}$$

 - *recall*

   > $$\frac{tp}{tp + fn}$$

 - $F_1$

   > $$\frac{2 \cdot precision \cdot recall}{precision + recall}$$

 - *micro* $F_1$

   > $F_1$ w którym $tp$, $fp$ i $fn$ są liczone łącznie dla wszystkich etykiet, tj. $tp = \sum_{e}{{tp}_e}$, $fn = \sum_{e}{{fn}_e}$, $fp = \sum_{e}{{fp}_e}$

 - *macro* $F_1$

   > średnia arytmetyczna z $F_1$ obliczonych dla poszczególnych etykiet z osobna.

Wyuczony model możemy wczytać z pliku korzystając z metody `load`.

In [45]:
model = SequenceTagger.load(modelPath)

2022-05-30 22:30:48,788 loading file slot-model/final-model.pt


Wczytany model możemy wykorzystać do przewidywania slotów w wypowiedziach użytkownika, korzystając
z przedstawionej poniżej funkcji `predict`.

In [47]:
def predict(model, sentence):
    csentence = [{'form': word} for word in sentence]
    fsentence = conllu2flair([csentence])[0]
    model.predict(fsentence)
    return [(token, ftoken.get_tag('slot').value) for token, ftoken in zip(sentence, fsentence)]

predict(model, 'poprosze bilet na batman'.split())

[('poprosze', 'O'), ('bilet', 'O'), ('na', 'O'), ('batman', 'B-title')]

Jak pokazuje przykład poniżej model wyuczony tylko na 100 przykładach popełnia w dosyć prostej
wypowiedzi błąd etykietując słowo `alarm` tagiem `B-weather/noun`.

In [12]:
tabulate(predict(model, 'kiedy gracie film zorro'.split()), tablefmt='html')

'<table>\n<tbody>\n<tr><td>kiedy </td><td>O/reqmore</td></tr>\n<tr><td>gracie</td><td>O/reqmore</td></tr>\n<tr><td>film  </td><td>O/reqmore</td></tr>\n<tr><td>zorro </td><td>O/reqmore</td></tr>\n</tbody>\n</table>'

In [43]:
# evaluation

def precision(tpScore, fpScore):
    return float(tpScore) / (tpScore + fpScore)

def recall(tpScore, fnScore):
    return float(tpScore) / (tpScore + fnScore)

def f1(precision, recall):
    return 2 * precision * recall/(precision + recall)

def eval():
    tp = 0
    fp = 0
    fn = 0
    sentences = [sentence for sentence in testset]
    for sentence in sentences:
        # get sentence as terms list
        termsList = [w["form"] for w in sentence]
        # predict tags
        predTags = [tag[1] for tag in predict(model, termsList)]
        
        # expTags = [token["slot"] + "/" + token["frame"] for token in sentence]
        expTags = [token["slot"] for token in sentence]

        for i in range(len(predTags)):
            if (expTags[i][0] == "O" and expTags[i] != predTags[i]):
                fp += 1
            elif ((expTags[i][0] != "O") & (predTags[i][0] == "O")):
                fn += 1
            elif ((expTags[i][0] != "O") & (predTags[i] == expTags[i])):
                tp += 1

    precisionScore = precision(tp, fp)
    recallScore = recall(tp, fn)
    f1Score = f1(precisionScore, recallScore)
    print("stats: ")
    print("precision: ", precisionScore)
    print("recall: ", recallScore)
    print("f1: ", f1Score)

eval()

    


KeyboardInterrupt



Literatura
----------
 1. Sebastian Schuster, Sonal Gupta, Rushin Shah, Mike Lewis, Cross-lingual Transfer Learning for Multilingual Task Oriented Dialog. NAACL-HLT (1) 2019, pp. 3795-3805
 2. John D. Lafferty, Andrew McCallum, and Fernando C. N. Pereira. 2001. Conditional Random Fields: Probabilistic Models for Segmenting and Labeling Sequence Data. In Proceedings of the Eighteenth International Conference on Machine Learning (ICML '01). Morgan Kaufmann Publishers Inc., San Francisco, CA, USA, 282–289, https://repository.upenn.edu/cgi/viewcontent.cgi?article=1162&context=cis_papers
 3. Sepp Hochreiter and Jürgen Schmidhuber. 1997. Long Short-Term Memory. Neural Comput. 9, 8 (November 15, 1997), 1735–1780, https://doi.org/10.1162/neco.1997.9.8.1735
 4. Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N. Gomez, Lukasz Kaiser, Illia Polosukhin, Attention is All you Need, NIPS 2017, pp. 5998-6008, https://arxiv.org/abs/1706.03762
 5. Alan Akbik, Duncan Blythe, Roland Vollgraf, Contextual String Embeddings for Sequence Labeling, Proceedings of the 27th International Conference on Computational Linguistics, pp. 1638–1649, https://www.aclweb.org/anthology/C18-1139.pdf


### Predykcja aktów mowy użytkownika

In [36]:
def conllu2flair(sentences, label2=None):
    fsentences = []

    for sentence in sentences:
        fsentence = Sentence()

        for token in sentence:
            ftoken = Token(token['form'])

            
            if label2:
                ftoken.add_tag(label2, token[label2])
                    
            fsentence.add_token(ftoken)

        fsentences.append(fsentence)

    return SentenceDataset(fsentences)

trainPath = "../tasks/zad8/pl/dataSentence/train.tsv"
testPath = "../tasks/zad8/pl/dataSentence/test.tsv"
dataFolder = "../tasks/zad8/pl/dataSentence"
column_name_map = {0: "text", 1: "label_topic"}
corpusClassification = CSVClassificationCorpus(dataFolder,
                                         column_name_map,
                                         skip_header=False,
                                         delimiter='\t',
)
print(corpusClassification)

2022-05-30 22:08:33,633 Reading data from ..\tasks\zad8\pl\dataSentence
2022-05-30 22:08:33,633 Train: ..\tasks\zad8\pl\dataSentence\train.tsv
2022-05-30 22:08:33,634 Dev: None
2022-05-30 22:08:33,635 Test: ..\tasks\zad8\pl\dataSentence\test.tsv
Corpus: 280 train + 31 dev + 32 test sentences


In [40]:
from flair.data import Corpus
from flair.datasets import TREC_6
from flair.embeddings import WordEmbeddings, FlairEmbeddings, DocumentRNNEmbeddings
from flair.models import TextClassifier
from flair.trainers import ModelTrainer

from os.path import exists


# 2. create the label dictionary
label_dict = corpusClassification.make_label_dictionary()

# 3. make a list of word embeddings
word_embeddings = [
    WordEmbeddings('pl'),
    FlairEmbeddings('polish-forward'),
    FlairEmbeddings('polish-backward'),
    CharacterEmbeddings(),
]

# 4. initialize document embedding by passing list of word embeddings
# Can choose between many RNN types (GRU by default, to change use rnn_type parameter)
document_embeddings = DocumentRNNEmbeddings(word_embeddings, hidden_size=256)

# 5. create the text classifier
classifier = TextClassifier(document_embeddings, label_dictionary=label_dict)

# 6. initialize the text classifier trainer
trainer = ModelTrainer(classifier, corpusClassification)

modelPath = 'resources/taggers/trec/final-model.pt'


fileExists = exists(modelPath)

if(not fileExists):
    # 7. start the training
    trainer.train('resources/taggers/trec',
                learning_rate=0.1,
                mini_batch_size=32,
                anneal_factor=0.5,
                patience=5,
                max_epochs=10)

2022-05-30 22:10:19,891 Computing label dictionary. Progress:


100%|██████████| 312/312 [00:04<00:00, 68.32it/s] 

2022-05-30 22:10:25,276 [b'inform', b'reqmore', b'hello', b'infomrm', b'reqmore inform', b'bye', b'ack', b'reqalts', b'impl-conf inform', b'help', b'request', b'affirm', b'thankyou', b'affirm inform', b'bye thankyou', b'hello inform', b'infrom', b'confirm', b'negate confirm', b'negate', b'negate ', b'deny']


In [41]:
classifier = TextClassifier.load(modelPath)

# create example sentence
sentence = Sentence('Jakie filmy gracie jutro?')

# predict class and print
classifier.predict(sentence)

print(sentence.labels)

2022-05-30 22:10:47,199 loading file resources/taggers/trec/final-model.pt
[reqmore (0.5459)]


In [42]:
# create example sentence
sentence = Sentence('siedzenia h1 h2')

# predict class and print
classifier.predict(sentence)

print(sentence.labels)

[inform (0.5967)]
